# Test spot detection

This is a test suite.

In [1]:
import scopyon

Set physical parameters.

In [2]:
config = scopyon.DefaultConfiguration()
config.update("""
default:
    magnification: 360
    detector:
        exposure_time: 0.033
""")

In [3]:
pixel_length = config.default.detector.pixel_length / config.default.magnification
L_2 = config.default.detector.image_size[0] * pixel_length * 0.5

Set the number of processes to enable `multiprocessing`:

In [4]:
config.environ.processes = 20

Prepare for generating inputs.

In [5]:
import numpy
rng = numpy.random.RandomState(123)
N = 1000

Collect data.

In [6]:
res = []
for _ in range(10):
    inputs = rng.uniform(-L_2, +L_2, size=(N, 2))
    img, infodict = scopyon.form_image(inputs, config=config, rng=rng, full_output=True)
    spots = scopyon.analysis.spot_detection(
        img.as_array(), min_sigma=1, max_sigma=4, threshold=40.0, overlap=0.5)
    res.append((inputs, img, infodict, spots))

/home/kaizu/environ/anaconda3/lib/python3.7/site-packages/skimage/feature/blob.py:125: RuntimeWarning: invalid value encountered in double_scalars
  r1 = blob1[-1] / blob2[-1]
/home/kaizu/environ/anaconda3/lib/python3.7/site-packages/skimage/feature/blob.py:126: RuntimeWarning: divide by zero encountered in true_divide
  pos1 = blob1[:ndim] / (max_sigma * root_ndim)
/home/kaizu/environ/anaconda3/lib/python3.7/site-packages/skimage/feature/blob.py:127: RuntimeWarning: divide by zero encountered in true_divide
  pos2 = blob2[:ndim] / (max_sigma * root_ndim)
/home/kaizu/environ/anaconda3/lib/python3.7/site-packages/skimage/feature/blob.py:129: RuntimeWarning: invalid value encountered in subtract
  d = np.sqrt(np.sum((pos2 - pos1)**2))
/home/kaizu/environ/anaconda3/lib/python3.7/site-packages/skimage/feature/blob.py:127: RuntimeWarning: invalid value encountered in true_divide
  pos2 = blob2[:ndim] / (max_sigma * root_ndim)
/home/kaizu/.local/share/virtualenvs/latest-mxc9Lo-B/lib/python3.

Find closest true positions from spots detected.

In [7]:
closest = []
for inputs, img, infodict, spots in res:
    data = numpy.array([(data[2], data[3]) for data in infodict['true_data'].values()])
    for spot in spots:
        distance = data - spot[0: 2]
        idx = (distance ** 2).sum(axis=1).argmin()
        closest.append(distance[idx])
closest = numpy.array(closest).T

Calculate average and std for the accuracy of the spot detection method.

In [8]:
print(f"Average along x-axis = {numpy.average(closest[0]):+.5f} pixels, std = {numpy.std(closest[0])}")
print(f"Average along y-axis = {numpy.average(closest[1]):+.5f} pixels, std = {numpy.std(closest[1])}")

Average along x-axis = +0.03475 pixels, std = 1.134670082759238
Average along y-axis = +0.00178 pixels, std = 1.1447345849828259


Show the heat map.

In [9]:
import plotly.express as px
H, xedges, yedges = numpy.histogram2d(x=closest[0], y=closest[1], bins=41, range=[[-2, +2], [-2, +2]])
fig = px.imshow(H, x=(xedges[: -1]+xedges[1: ])*0.5, y=(yedges[: -1]+yedges[1: ])*0.5)
fig.show()